In [28]:
import pandas as pd
import plotly.express as px
import numpy as np
import plotly.graph_objects as go


In [10]:
"""
eth_usd_rates ETH to USD price

6924 -- unique tokens were saled
10000 -- unique tokens in total
"""

eth_usd_rates = pd.read_csv('data/eth_usd_fx_rates.csv')
eth_usd_rates['date'] = pd.to_datetime(eth_usd_rates["date"], dayfirst=True)

token_metadata = pd.read_csv('data/token_metadata.csv')

token_sales = pd.read_csv('data/token_sales.csv')[['token_index', 'timestamp', 'eth', 'usd']]
token_sales['datetime'] = pd.to_datetime(token_sales['timestamp'],unit='s')
token_sales['date'] = token_sales['datetime'].dt.date

# Join two tables with keeping all tokens
token_data = token_metadata.merge(token_sales, on='token_index', how='left')

In [7]:
# Market state can be described as amount of sales and eth to usd ratio
fig = px.histogram(token_sales, x="date")
fig.update_layout(title='Tokens sales count')
fig.show()

fig = px.bar(token_sales.groupby('date')['date'].count().reset_index(name='count'), x='date', y='count')
fig.update_layout(title='Tokens sales count')
fig.show()


In [35]:
eth_usd_rates['sma30'] = eth_usd_rates['open'].rolling(30).mean()
eth_usd_rates['sma7'] = eth_usd_rates['open'].rolling(7).mean()

#eth_usd_rates['ema7'] = eth_usd_rates['open'].ewm(span=7, adjust=False).mean()

eth_usd_rates['diff30'] = eth_usd_rates['sma30'].diff(periods=1)
eth_usd_rates['diff7'] = eth_usd_rates['sma7'].diff(periods=1)

fig = go.Figure()
fig.add_trace(go.Scatter(x=eth_usd_rates['date'], y=eth_usd_rates['open'], mode='lines', name='open'))
fig.add_trace(go.Scatter(x=eth_usd_rates['date'], y=eth_usd_rates['sma30'], mode='lines', name='sma30'))
fig.add_trace(go.Scatter(x=eth_usd_rates['date'], y=eth_usd_rates['sma7'], mode='lines', name='sma7'))
# fig.add_trace(go.Scatter(x=eth_usd_rates['date'], y=eth_usd_rates['ema7'], mode='lines', name='ema7'))


fig.add_trace(go.Scatter(x=eth_usd_rates['date'], y=eth_usd_rates['diff30'], mode='lines', name='diff30'))
fig.add_trace(go.Scatter(x=eth_usd_rates['date'], y=eth_usd_rates['diff7'], mode='lines', name='diff7'))

fig.update_layout(title='ETH rpice')
fig.show()

In [11]:
fig = px.bar(token_data['Skin Tone'].value_counts().rename_axis('Skin Tone').reset_index(name='count')
            , x='Skin Tone', y='count')
fig.update_layout(title='Skin Tone count')
fig.show()


In [12]:
fig = px.bar(token_data.groupby('Skin Tone')['usd'].mean().reset_index(), x='Skin Tone', y='usd')
fig.update_layout(title='AVG price in USD by Skin Tone')
fig.show()

In [14]:
fig = px.scatter(token_data, x="date", y="usd", color='Skin Tone')
fig.update_layout(title='Token sales in USD by Skin Tone')
fig.show()
fig = px.scatter(token_data, x="date", y="eth", color='Skin Tone')
fig.update_layout(title='Token sales in ETH by Skin Tone')
fig.show()

In [18]:
fig = px.histogram(token_metadata, x=np.log(token_metadata["rarity_score"]))
fig.update_layout(title='Token rarity_score distribution')
fig.show()

In [25]:
fig = px.scatter(token_data, x="date", y="usd", color=np.log(token_data["rarity_score"]), symbol='Skin Tone')
fig.update_layout(title='Token sales in USD by Skin Tone and rarity_score')
fig.update_layout(coloraxis_colorbar=dict(yanchor="top", y=1, x=0,
                                          ticks="outside",
                                          ticksuffix=" bills"))
fig.show()

In [16]:
fig = px.bar((token_data.isna().sum() / len(token_data)).rename_axis('feature').reset_index(name='fraction'), 
             x='feature', y='fraction')
fig.update_layout(title='Missing values fraction')
fig.show()